# Preparing data for passim

These scripts are used to prepare the data for the passim alignment process.
  
The input datas are the xml altos from eScriptorium containing the OCR text,
and the digital editions from Sefaria (cleaned and concatenated with this pipeline:
https://github.com/Freymat/from_Sefaria_to_Passim).

The output file, that will be processed with passim is a jsonl file, each line of which is a dictionary containing
either:
- the content of an OCR textblock. These textblocks are constituted by the concatenation of the text of the OCR lines, from a part region.
  The content of the OCR lines is retrieved from the xmls alto files from eScriptorium.
- the text of a digital edition (Ground Truth), concatenated in one line. Those texts are retrieved from Sefaria, cleanded and concatenated.

Passim will then align the OCR textblocks with the Ground Truth texts, and will output a jsonl file containing the alignment.

### Importing Required Libraries

In [61]:
import json # To work with JSON data
import jsonlines # To write data in JSON Lines format
import os # To interact with the operating system
import glob # To search for files in a directory
from xml.etree import ElementTree # To parse XML files
import subprocess # To run Passim
from pprint import pprint

# Import functions for eScriptorium's API
from functions import *

### Initializing

In [62]:
# ground truth files
GT_texts_path = "digital_editions"

# xmls files from eScriptorium (OCR results) /path
xmls_directory_path = "xmls_from_eSc"

# output file / path for the JSON file that will be used as input for Passim
output_file = "json_for_passim/passim_input.json" # path for the output JSON file. This file will be used as input for Passim.


In [63]:
# Initialize the list where output datas for Passim will be stored
output_data = []

### Build the content of OCR textblocks and prepare them for Passim

#### Loop through XML files from eSC, and extract TextLine elements text and ID

In [64]:
import glob
import os
from xml.etree import ElementTree
from pprint import pprint

""" This script reads the XML alto files produced by eScriptorium,
extracts and concatenate the text of the lines from each TextBlock elements.

The result is a list of dictionaries, one per alto file.
Each dictionnary contains the list of the text blocks in the file. Each element of this list is a dictionary containing:
- the concatenated text of the lines in the TextBlock element,
- the ID of the TextBlock element,
- the IDs of the TextLine elements in the text block, and the starting position of each line in the concatenated text.
"""

# Path to directory containing XML files
xmls_directory_path = "xmls_from_eSc"

# Initialize list to store parts
parts = []

# Loop through all XML files in the directory
for filename in glob.glob(os.path.join(xmls_directory_path, "*.xml")):
    # Obtenir le nom de chaque fichier
    basename = os.path.splitext(os.path.basename(filename))[0]

    # Initialize list to store text blocks
    blocks = []

    # Parse the XML file
    tree = ElementTree.parse(filename)
    root = tree.getroot()

    # Loop through all TextBlock elements in the XML file
    for text_block in root.iter("{http://www.loc.gov/standards/alto/ns-v4#}TextBlock"):
        # Obtenir l'ID de l'attribut ID de l'élément TextBlock
        text_block_id = text_block.get("ID")

        lines = []
        continuous_text = ""
        char_count = 0  # Initial position for continuous text

        # Loop through all TextLine elements in the TextBlock element
        for text_line in text_block.iter("{http://www.loc.gov/standards/alto/ns-v4#}TextLine"):
            text = text_line.find("{http://www.loc.gov/standards/alto/ns-v4#}String").get("CONTENT").strip()

            line_dict = {
                "line_id": text_line.get("ID"),
                "start": char_count,  # Start position of line in continuous text
                "end" : char_count + len(text) -1,
                "length": len(text),
                "text": text
            }
            separator = "\n"
            continuous_text += (text + separator)
            char_count += len(text + separator)  # Updates the starting position for the next line.

            lines.append(line_dict)

        # Add text block to block list
        blocks.append({
            "ocr_block_text": continuous_text.strip(),  # Removes superfluous spaces at the beginning and end
            "text_block_id": text_block_id,
            "ocr_lines": lines,
            "series": 'OCR'  # Distinguishes OCR from control
        })

    # Ajouter un document avec ses blocs correspondants à la liste des parties

    parts.append({
        "filename": basename,
        "ocr_blocks": blocks
    })

# Save the 'parts' dictionnary to a JSON file named lines_dict
if not os.path.exists("ocr_lines_dict"):
    os.makedirs("ocr_lines_dict")

# Save the 'parts' dictionnary to a JSON file
with open("ocr_lines_dict/ocr_lines_dict.json", "w", encoding="utf-8") as f:
    json.dump(parts, f, ensure_ascii=False, indent=4)

pprint(parts)


[{'filename': 'IE103402206_00010',
  'ocr_blocks': [{'ocr_block_text': 'וידבר יהוה אל-משה במדבר סיני\n'
                                    'באהל מועד באחד לחדש השני בשנה\n'
                                    'השנית לצאתם מארץ מצרים לאמר: בשאו\n'
                                    'את-ראש כל-עדת בני-ישראל למשפחתם\n'
                                    'לבית אבתם במספר שמות כל--זכר\n'
                                    'לגלגלתם: ג) מבן עשרים שנה ומעלה כל-\n'
                                    'יצא צבא בישראל תפקדו אתם לצבאתם\n'
                                    'אתה ואהרן: ד ואתכם יהיו איש איש למטה\n'
                                    'איש ראש לבית-אבתיו הוא: ה ואלה שמות\n'
                                    'האנשים אשר יעמדו אתכם לראובן אליצור\n'
                                    'בן-שדיאור:ו לשמעון שלמיאל בן-צורישדי:',
                  'ocr_lines': [{'end': 27,
                                 'length': 28,
                                 'line_id': 'eSc_line_72278199',
 

#### Build the input data for passim, from the OCR line dictionnary

In [65]:
# open the dictionnary
with open("ocr_lines_dict/ocr_lines_dict.json", "r", encoding="utf-8") as f:
    parts = json.load(f)
    
output_data = []
for part in parts:
    for block in part["ocr_blocks"]:
        text_block_id = block["text_block_id"]
        text_block_text = block["ocr_block_text"]
        filename = part["filename"]
        output_data.append({"id": text_block_id +'_' + filename, "series": 'OCR',"ref": '0', "text": text_block_text})
        print(text_block_id, filename)
print(output_data)


eSc_textblock_f8f9ef30 IE103402206_00010
eSc_textblock_11cd7539 IE103402206_00014
eSc_textblock_feba6aab IE103402206_00014
eSc_textblock_769d627c IE103409244_00025
eSc_textblock_7e5a2f47 IE34120895_00033
eSc_textblock_a2bebbd5 IE34120895_00046
eSc_textblock_2a8e50d7 IE34120895_00054
eSc_textblock_86f48ed1 IE35481905_00011
eSc_textblock_b28ad8a9 IE35481905_00024
eSc_textblock_d7345649 IE35481905_00027
eSc_textblock_5930d386 IE36149273_00006
eSc_textblock_e29fc12c IE36149273_00009
eSc_textblock_08543a85 IE36149273_00015
eSc_textblock_205c5b63 IE61220167_00083
eSc_textblock_ab76e7e2 IE61220167_00084
eSc_textblock_2594389a IE61220167_00097
[{'id': 'eSc_textblock_f8f9ef30_IE103402206_00010', 'series': 'OCR', 'ref': '0', 'text': 'וידבר יהוה אל-משה במדבר סיני\nבאהל מועד באחד לחדש השני בשנה\nהשנית לצאתם מארץ מצרים לאמר: בשאו\nאת-ראש כל-עדת בני-ישראל למשפחתם\nלבית אבתם במספר שמות כל--זכר\nלגלגלתם: ג) מבן עשרים שנה ומעלה כל-\nיצא צבא בישראל תפקדו אתם לצבאתם\nאתה ואהרן: ד ואתכם יהיו איש איש למטה\

### Build the GT text datas for Passim
Add every txt file in the GT directory to the output data

In [66]:
for root, dirs, files in os.walk(GT_texts_path):
    for file in files:
        if file.endswith(".txt"):
            text_file = os.path.join(root, file)
            with open(text_file, "r", encoding="utf-8") as f:
                text = f.read()
                filename = os.path.basename(text_file)
                output_data.append({"id": filename, "series": 'GT', "ref": '1', "text": text})
                print(f"Added to output: {filename}: {text}")
                print(filename)

print(output_data)

Added to output: MT_NoVoc_concatenated.txt: בראשית ברא אלהים את השמים ואת הארץ : והארץ היתה תהו ובהו וחשך על פני תהום ורוח אלהים מרחפת על פני המים : ויאמר אלהים יהי אור ויהי אור : וירא אלהים את האור כי טוב ויבדל אלהים בין האור ובין החשך : ויקרא אלהים לאור יום ולחשך קרא לילה ויהי ערב ויהי בקר יום אחד : ויאמר אלהים יהי רקיע בתוך המים ויהי מבדיל בין מים למים : ויעש אלהים את הרקיע ויבדל בין המים אשר מתחת לרקיע ובין המים אשר מעל לרקיע ויהי כן : ויקרא אלהים לרקיע שמים ויהי ערב ויהי בקר יום שני : ויאמר אלהים יקוו המים מתחת השמים אל מקום אחד ותראה היבשה ויהי כן : ויקרא אלהים ליבשה ארץ ולמקוה המים קרא ימים וירא אלהים כי טוב : ויאמר אלהים תדשא הארץ דשא עשב מזריע זרע עץ פרי עשה פרי למינו אשר זרעו בו על הארץ ויהי כן : ותוצא הארץ דשא עשב מזריע זרע למינהו ועץ עשה פרי אשר זרעו בו למינהו וירא אלהים כי טוב : ויהי ערב ויהי בקר יום שלישי : ויאמר אלהים יהי מארת ברקיע השמים להבדיל בין היום ובין הלילה והיו לאתת ולמועדים ולימים ושנים : והיו למאורת ברקיע השמים להאיר על הארץ ויהי כן : ויעש אלהים את שני המארת ה

### Writing Data to JSONLines File in Compact Format without ASCII Encoding, for Passim

In [67]:
# Open the output file in write mode
with open(output_file, "w", encoding="utf-8") as f:
    # Create a jsonlines writer object that writes to the output file
    writer = jsonlines.Writer(f)
    # Loop through each item in the output_data list
    for item in output_data:
        # Write the current item to the output file using the jsonlines writer
        writer.write(item)

In [68]:
print(f"Output file created: {output_file}")

Output file created: json_for_passim/passim_input.json


# Composing the command to run Passim

In [69]:
# Command Line to request an interactive session on HTC
t = "6:00:00" # Session duration - hours:minutes:seconds
n_cores = 123 # number of cpu cores
mem = "64G" # memory per node    
# % srun -t 0-08:00 -n 4 --mem 2G --pty bash -i

command_srun = f"srun -t {t} -n {n_cores} --mem {mem} --pty bash -i"
print(f"Session interactive HTC:\n{command_srun}")


Session interactive HTC:
srun -t 6:00:00 -n 123 --mem 64G --pty bash -i


In [78]:
# Command Line to request an interactive session on HTC
# example: % srun -t 0-08:00 -n 4 --mem 2G --pty bash -i
t = "6:00:00" # Session duration - hours:minutes:seconds
n_cores = 4 # number of cpu cores
mem = 6 # memory per node, in GB    

command_srun = f"srun -t {t} -n {n_cores} --mem {mem}G --pty bash -i"

# Command Line to run Passim

n = 7 # n-gram order (default: 25) 
# m = 5 # Minimum number of n-gram matches between document (default: 5)
# a = 7 # Minimum length of alignment (default: 50)
# g = 25 # Minimum size of gap that separates passages (default: 600)
align_mode = 'docwise' # alignment mode

input_file = "json_for_passim/passim_input.json" # input file for Passim
output_folder = f"json_from_passim/out_n{n}_{align_mode}_all-pairs"

command_passim = f"SPARK_SUBMIT_ARGS='--master local[{n_cores}] --executor-memory {mem}G --driver-memory 4G' seriatim --{align_mode} --floating-ngrams --fields ref --filterpairs 'ref = 1 AND ref2 = 0' --all-pairs -n {n} {input_file} {output_folder}"

print(f"Session interactive HTC:\n{command_srun}")
print(f"Passim command line:\n{command_passim}")

Session interactive HTC:
srun -t 6:00:00 -n 4 --mem 6G --pty bash -i
Passim command line:
SPARK_SUBMIT_ARGS='--master local[4] --executor-memory 6G --driver-memory 4G' seriatim --docwise --floating-ngrams --fields ref --filterpairs 'ref = 1 AND ref2 = 0' --all-pairs -n 7 json_for_passim/passim_input.json json_from_passim/out_n7_docwise_all-pairs


In [71]:
# Executing passim locally
subprocess.run(command_passim, shell=True)

https://repos.spark-packages.org/ added as a remote repository with the name: repo-1
Ivy Default Cache set to: /home/matthieu/.ivy2/cache
The jars for the packages stored in: /home/matthieu/.ivy2/jars
graphframes#graphframes added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-3838ba06-65fe-4016-920c-5b39d4fd5b21;1.0
	confs: [default]


:: loading settings :: url = jar:file:/home/matthieu/anaconda3/envs/acdc/lib/python3.9/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


	found graphframes#graphframes;0.8.0-spark3.0-s_2.12 in spark-packages
	found org.slf4j#slf4j-api;1.7.16 in central
:: resolution report :: resolve 148ms :: artifacts dl 4ms
	:: modules in use:
	graphframes#graphframes;0.8.0-spark3.0-s_2.12 from spark-packages in [default]
	org.slf4j#slf4j-api;1.7.16 from central in [default]
	---------------------------------------------------------------------
	|                  |            modules            ||   artifacts   |
	|       conf       | number| search|dwnlded|evicted|| number|dwnlded|
	---------------------------------------------------------------------
	|      default     |   2   |   0   |   0   |   0   ||   2   |   0   |
	---------------------------------------------------------------------
:: retrieving :: org.apache.spark#spark-submit-parent-3838ba06-65fe-4016-920c-5b39d4fd5b21
	confs: [default]
	0 artifacts copied, 2 already retrieved (0kB/6ms)


Namespace(id='id', text='text', locs='locs', pages='pages', minDF=2, maxDF=100, min_match=5, n=7, floating_ngrams=True, complete_lines=False, gap=600, max_offset=20, beam=20, pcopy=0.8, min_align=50, src_overlap=0.9, dst_overlap=0.5, fields=['ref'], filterpairs='ref = 1 AND ref2 = 0', all_pairs=True, pairwise=False, docwise=True, linewise=False, to_pairs=False, to_extents=False, link_model=None, link_features=None, log_level='WARN', input_format='json', output_format='json', inputPath='json_for_passim/passim_input.json', outputPath='json_from_passim/out_n7_docwise_all-pairs')
13:42:48.673 [Thread-5] WARN  org.apache.spark.sql.catalyst.util.SparkStringUtils - Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


CompletedProcess(args="SPARK_SUBMIT_ARGS='--master local[4] --executor-memory 6G --driver-memory 4G' seriatim --docwise --floating-ngrams --fields ref --filterpairs 'ref = 1 AND ref2 = 0' --all-pairs -n 7 json_for_passim/passim_input.json json_from_passim/out_n7_docwise_all-pairs", returncode=0)

In [85]:
# Display passim output

passim_output = []

for file_path in glob.glob(f"{output_folder}/out.json/*.json"):
    with open(file_path, "r", encoding="utf-8") as f:
        for line in f:
            data = json.loads(line)
            passim_output.append(data)

pprint(passim_output[0])
print(len(passim_output[0]['lines']))


{'id': 'eSc_textblock_f8f9ef30_IE103402206_00010',
 'lines': [{'begin': 0,
            'text': 'וידבר יהוה אל-משה במדבר סיני\n',
            'wits': [{'alg': 'וידבר יהוה אל משה במדבר סיני ',
                      'alg2': 'וידבר יהוה אל‐משה במדבר סיני\n',
                      'begin': 242880,
                      'id': 'MT_NoVoc_concatenated.txt',
                      'matches': 28,
                      'ref': '1',
                      'series': 'GT',
                      'text': 'וידבר יהוה אל משה במדבר סיני '}]},
           {'begin': 29,
            'text': 'באהל מועד באחד לחדש השני בשנה\n',
            'wits': [{'alg': 'באהל מועד באחד לחדש השני בשנה ',
                      'alg2': 'באהל מועד באחד לחדש השני בשנה\n',
                      'begin': 242909,
                      'id': 'MT_NoVoc_concatenated.txt',
                      'matches': 30,
                      'ref': '1',
                      'series': 'GT',
                      'text': 'באהל מועד באחד לחדש השני בשנה 

In [86]:
for textblock in passim_output:
    print(f"Document ID: {textblock['id']}")
    print(f"Number of lines: {len(textblock['lines'])}")
    print("")

Document ID: eSc_textblock_f8f9ef30_IE103402206_00010
Number of lines: 11

Document ID: eSc_textblock_769d627c_IE103409244_00025
Number of lines: 28

Document ID: eSc_textblock_11cd7539_IE103402206_00014
Number of lines: 9

Document ID: eSc_textblock_ab76e7e2_IE61220167_00084
Number of lines: 19

Document ID: eSc_textblock_7e5a2f47_IE34120895_00033
Number of lines: 31

Document ID: eSc_textblock_2594389a_IE61220167_00097
Number of lines: 19

Document ID: eSc_textblock_205c5b63_IE61220167_00083
Number of lines: 19

Document ID: eSc_textblock_d7345649_IE35481905_00027
Number of lines: 18



In [88]:
# display eSc_textblock_2594389a_IE61220167_00097
for textblock in passim_output:
    if textblock['id'] == 'eSc_textblock_2594389a_IE61220167_00097':
        pprint(textblock['lines'])

[{'begin': 0, 'text': 'רבונו של עולם כבו שכבש רחמיו לעשות\n'},
 {'begin': 35,
  'text': 'רצונך בלבב שלם כן יכבשו רחמיך\n',
  'wits': [{'alg': 'רצונך--------- כן יכבשו רחמיך ',
            'alg2': 'רצונך בלבב שלם כן יכבשו רחמיך\n',
            'begin': 95594,
            'id': 'Machzor_Yom_Kippur_Ashkenaz_clean_concatenated.txt',
            'matches': 21,
            'ref': '1',
            'series': 'GT',
            'text': 'רצונך כן יכבשו רחמיך '},
           {'alg': 'רצונך--------- כן יכבשו רחמיך ',
            'alg2': 'רצונך בלבב שלם כן יכבשו רחמיך\n',
            'begin': 9855,
            'id': 'Siddur_Ashkenaz_clean_concatenated.txt',
            'matches': 21,
            'ref': '1',
            'series': 'GT',
            'text': 'רצונך כן יכבשו רחמיך '}]},
 {'begin': 65,
  'text': 'את בעסך ‧ ויגולו רחמיך על מדותיך ותתגהג\n',
  'wits': [{'alg': 'את כעסך מעלינו ויג-לו רחמיך על מדותיך, ותכנס אתנו לפנים '
                   'משורת דינך ותתנהג ',
            'alg2': 'את בעסך ----